In [1]:
import pandas as pd
import os, json

In [2]:
df = pd.read_csv("./data/network_en_mc.csv")
df

name  zero_native zero_self_con     zero_cot  \
0       Baichuan-13B-Chat         18.3          20.4         28.6   
1    Chinese-Alpaca-2-13B         37.7          37.7         49.7   
2           GPT-3.5-turbo         66.6          66.8         69.6   
3             LLaMA-2-13B         41.8          46.5         53.1   
4            Qwen-7B-Chat         45.9            46         47.3   
5             ChatGLM2-6B         24.8          24.7         36.6   
6     Chinese-LLaMA-2-13B         29.4          29.4         37.8   
7             InternLM-7B         38.7          38.7         43.9   
8              LLaMA-2-7B         39.5            40         45.4   
9      Baichuan2-13B-Chat         14.1          15.3         24.1   
10                  GPT-4            /             /            /   
11        AquilaChat2-34B        36.63         36.63        44.83   
12            Yi-34B-Chat        57.75         59.14        65.11   
13  DevOps-Model-14B-Chat        30.69         30.59        55.77   
14          Qwen-72B-Chat        70.41         70.50        72.38   
15             Mistral-7B        29.27         29.27        46.30   
16          Qwen-14B-Chat        43.78         47.81        56.58   
17       LLaMA-2-70B-Chat        25.29         25.29        57.97   
18          ERNIE-Bot-4.0        61.15         61.15        70.00   
19            ChatGLM3-6B  43.38487973   43.38487973  44.58762887   
20     InternLM2-Chat-20B  56.35738832   56.35738832  26.18025751   
21      InternLM2-Chat-7B  49.74226804   49.74226804  56.18556701   
22               gemma_2b     26.46048      26.46048     33.41924   
23               gemma_7b     25.08591      25.08591     50.85911   
24       qwen1.5-14b-base     34.87973      34.87973     60.82474   
25       qwen1.5-14b-chat     54.89691       56.4433     64.08935   

   zero_cot_self_con   few_native few_self_con    few_cot  few_cot_self_con  
0                 37         24.1         26.7  18.200000         17.800000  
1               49.7         48.6         48.6  50.500000         50.500000  
2                 72         68.3         68.3  70.900000         72.500000  
3               58.7         53.3           53  56.800000         61.000000  
4               50.1         52.1           51  48.300000         49.800000  
5               36.5         37.6         37.6  40.500000         40.500000  
6               37.8         40.4         40.4  28.800000         28.800000  
7               43.9         45.2         45.2  51.400000         51.400000  
8               49.5         48.2         46.8  52.000000         55.200000  
9               25.8         32.3         33.1  25.600000         27.700000  
10                 /            /            /  88.700000         88.700000  
11             44.83        46.65        46.65        NaN               NaN  
12             68.79        68.16        68.37  78.090000         80.060000  
13             63.63        63.85        61.96  41.150000         44.010000  
14             72.56        70.32        70.32  70.130000         70.220000  
15             46.30        47.22        47.22  45.580000         45.580000  
16             59.40        62.09        59.70  49.060000         55.880000  
17             58.06        52.97        52.97  58.550000         58.550000  
18             70.00        60.00        60.00  70.000000         70.000000  
19       44.58762887  42.09621993  42.09621993  43.470790         43.470790  
20       26.18025751  60.48109966  60.48109966  45.103093         45.103093  
21       56.18556701  48.19587629  48.19587629  49.742268         49.742268  
22         33.41924       26.6323      26.6323  37.542960         37.542960  
23         50.85911      30.24055     30.24055  51.557470         51.557470  
24         60.82474      65.54983     65.54983  47.079040         47.079040  
25          67.09622     52.23368     53.52234  59.536080         64.175260

In [20]:
def process_mc_df(df):
    # 将name列重命名为Model
    df = df.rename(columns={"name": "Model"})
    # 将zero_naive, zero_self_con, zero_cot, zero_cot_self_con, few_naive, few_self_con, few_cot, few_cot_self_con列重新组织成MultiIndex，一层为Zeroshot, Fewshot,一层为Naive, Self-Consistency, CoT, CoT+Self-Consistency
    df = df.set_index("Model")
    # df = df.stack().unstack()
    df.columns = pd.MultiIndex.from_tuples([("Zeroshot", "Naive"), ("Zeroshot", "SC"), ("Zeroshot", "CoT"), ("Zeroshot", "CoT+SC"), ("Fewshot", "Naive"), ("Fewshot", "SC"), ("Fewshot", "CoT"), ("Fewshot", "CoT+SC")])
    # 将除了Model列之外的列的value转换为数值型，失败的为NaN
    df = df.apply(pd.to_numeric, errors="coerce")
    # 显示小数点后两位
    df = df.round(2)
    # 给每一行添加一列BestScore
    df["BestScore"] = df.max(axis=1)
    # 根据BestScore给df排序
    df = df.sort_values(by="BestScore", ascending=False)
    # 
    df = df.reset_index()
    return df

processed = process_mc_df(df)
processed.columns
processed['Zeroshot']

Naive     SC    CoT  CoT+SC
0     NaN    NaN    NaN     NaN
1   57.75  59.14  65.11   68.79
2   70.41  70.50  72.38   72.56
3   66.60  66.80  69.60   72.00
4   61.15  61.15  70.00   70.00
5   54.90  56.44  64.09   67.10
6   34.88  34.88  60.82   60.82
7   30.69  30.59  55.77   63.63
8   43.78  47.81  56.58   59.40
9   41.80  46.50  53.10   58.70
10  56.36  56.36  26.18   26.18
11  25.29  25.29  57.97   58.06
12  49.74  49.74  56.19   56.19
13  39.50  40.00  45.40   49.50
14  45.90  46.00  47.30   50.10
15  25.09  25.09  50.86   50.86
16  38.70  38.70  43.90   43.90
17  37.70  37.70  49.70   49.70
18  29.27  29.27  46.30   46.30
19  36.63  36.63  44.83   44.83
20  43.38  43.38  44.59   44.59
21  24.80  24.70  36.60   36.50
22  29.40  29.40  37.80   37.80
23  26.46  26.46  33.42   33.42
24  18.30  20.40  28.60   37.00
25  14.10  15.30  24.10   25.80